In [47]:

from __future__ import print_function, division

from keras.datasets import mnist
from keras.datasets import cifar10
from keras.layers import Input, Dense, Reshape, Flatten, Dropout, merge
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from keras.optimizers import Adam
from keras.layers import Concatenate, Dense, LSTM, Input, concatenate
 

import tensorflow as tf
from scipy.misc import imread, imsave

import matplotlib.pyplot as plt

import sys
import os
from PIL import Image
from glob import glob

import numpy as np


In [48]:
from keras.models import load_model

In [49]:
class GAN():
    
    
    def __init__(self):
        self.img_rows = 28
        self.img_cols = 28
        self.channels = 3
        self.img_shape = (1,self.img_rows*self.img_cols*self.channels)

        optimizer = Adam(0.0002, 0.5)

        # Build and compile the discriminator
        self.discriminator = self.build_discriminator()
        self.discriminator.compile(loss='binary_crossentropy',
            optimizer=optimizer,
            metrics=['accuracy'])

        # Build the generator
        self.generator = self.build_generator()
       

        # The generator takes noise as input and generated imgs
        z = Input(shape=(4596,))
        img = self.generator(z)
        
        img_merge = concatenate([img,z], axis=1)
        print ("img_merge")
        print (img_merge)
        print (img_merge.shape)

        # For the combined model we will only train the generator
        self.discriminator.trainable = False

        # The valid takes generated images as input and determines validity
        valid = self.discriminator(img_merge)

        # The combined model  (stacked generator and discriminator) takes
        # noise as input => generates images => determines validity
        self.combined = Model(z, valid)
        self.combined.compile(loss='binary_crossentropy', optimizer=optimizer)

    def build_generator(self):

        noise_shape = (4596,)

        model = Sequential()

        model.add(Dense(256, input_shape=noise_shape))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(512))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(1024))
        model.add(LeakyReLU(alpha=0.2))
        model.add(BatchNormalization(momentum=0.8))
        model.add(Dense(np.prod(self.img_shape), activation='tanh'))
        
        #model.add(Reshape(self.img_shape))

        model.summary()

        noise = Input(shape=noise_shape)
        img = model(noise)

        #img = Concatenate([img,noise])
        
        return Model(noise, img)
 

    def build_discriminator(self):

        #img_shape = (self.img_rows, self.img_cols, self.channels)
        img_shape = (self.img_rows*self.img_cols*self.channels+4596,)

        model = Sequential()

        #model.add(Flatten(input_shape=img_shape))
        model.add(Dense(512, input_shape=img_shape))
        #model.add(Dense(512))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(256))
        model.add(LeakyReLU(alpha=0.2))
        model.add(Dense(1, activation='sigmoid'))
        model.summary()

        img = Input(shape=img_shape)
        validity = model(img)

        return Model(img, validity)

    def get_image(self, image_path, width, height, mode):

        image = Image.open(image_path)
        # image = image.resize([width, height], Image.BILINEAR)
        if image.size != (width, height):
        # Remove most pixels that aren't part of a face
            face_width = face_height = 108
            j = (image.size[0] - face_width) // 2
            i = (image.size[1] - face_height) // 2
            image = image.crop([j, i, j + face_width, i + face_height])
            image = image.resize([width, height])

        return np.array(image.convert(mode))

    def get_batch(self, image_files, width, height, mode):
        data_batch = np.array(
            [self.get_image(sample_file, width, height, mode) for sample_file in image_files])

        return data_batch

    def train(self, epochs, batch_size=128, save_interval=50):

        X_train_green_fr = self.get_batch(glob(os.path.join('data_final/green_fruit', '*'))[:490], 28, 28, 'RGB')
        X_train_purple_fr = self.get_batch(glob(os.path.join('data_final/purple_fruit', '*'))[:490], 28, 28, 'RGB')
        X_train_red_fl = self.get_batch(glob(os.path.join('data_final/red_flower', '*'))[:322], 28, 28, 'RGB')
        X_train_yellow_fl = self.get_batch(glob(os.path.join('data_final/yellow_flower', '*'))[:490], 28, 28, 'RGB')
        
        
        
        
        
        
        
        y_train_green_fr = np.genfromtxt('embeddings/greenpear.csv',delimiter=",").reshape(1,4096);
        y_train_purple_fr = np.genfromtxt('embeddings/purplepear.csv',delimiter=",").reshape(1,4096); 
        y_train_red_fl = np.genfromtxt('embeddings/redbanana.csv',delimiter=",").reshape(1,4096);
        y_train_yellow_fl = np.genfromtxt('embeddings/yellowbanana.csv',delimiter=",").reshape(1,4096); 
        
     
        
        
        
        
        
        #print(X_train_blue_fl.shape)
        # Rescale -1 to 1
        X_train_green_fr = (X_train_green_fr.astype(np.float32) - 127.5) / 127.5
        X_train_purple_fr = (X_train_purple_fr.astype(np.float32) - 127.5) / 127.5
        X_train_red_fl = (X_train_red_fl.astype(np.float32) - 127.5) / 127.5
        X_train_yellow_fl = (X_train_yellow_fl.astype(np.float32) - 127.5) / 127.5
        # Adversarial ground truth
        valid = np.ones((batch_size, 1))
        fake = np.zeros((batch_size, 1))

        for epoch in range(epochs):

            # ---------------------
            #  Train Discriminator
            # ---------------------
            
            
            
            
            G_repeated = np.asarray([y_train_green_fr,]*int(batch_size/4))
            P_repeated = np.asarray([y_train_purple_fr,]*int(batch_size/4))
            R_repeated = np.asarray([y_train_red_fl,]*int(batch_size/4))
            Y_repeated = np.asarray([y_train_yellow_fl,]*int(batch_size/4))
            
            
            
            
            

            # Sample a random batch of images
            idx = np.random.randint(0, X_train_green_fr.shape[0], int(batch_size/4))
            imgs_green_fr = X_train_green_fr[idx]
            
            #appending with embedding blue flowers
            print (imgs_green_fr.shape)
            print (G_repeated.shape)
            
            #reshaping
            imgs_green_fr = imgs_green_fr.reshape(int(batch_size/4),28*28*3)
            G_repeated = G_repeated.reshape(int(batch_size/4),4096)

            imgs_green_fr_with_emb = np.concatenate((imgs_green_fr, G_repeated),axis=1)
            
            
            
            
            
            # Sample a random batch of images
            idx = np.random.randint(0, X_train_purple_fr.shape[0], int(batch_size/4))
            imgs_purple_fr = X_train_purple_fr[idx]
            
            #reshaping
            imgs_purple_fr = imgs_purple_fr.reshape(int(batch_size/4),28*28*3)
            P_repeated = P_repeated.reshape(int(batch_size/4),4096)
            
            #appending with embedding purple fruit
            imgs_purple_fr_with_emb = np.concatenate((imgs_purple_fr, P_repeated),axis=1)
            
            
            
            
            
            
            
            # Sample a random batch of images
            idx = np.random.randint(0, X_train_red_fl.shape[0], int(batch_size/4))
            imgs_red_fl = X_train_red_fl[idx]
            
            #appending with embedding blue flowers
            
            #reshaping
            imgs_red_fl = imgs_red_fl.reshape(int(batch_size/4),28*28*3)
            R_repeated = R_repeated.reshape(int(batch_size/4),4096)

            imgs_red_fl_with_emb = np.concatenate((imgs_red_fl, R_repeated),axis=1)
            
            
            
            
            
            
            
            # Sample a random batch of images
            idx = np.random.randint(0, X_train_yellow_fl.shape[0], int(batch_size/4))
            imgs_yellow_fl = X_train_yellow_fl[idx]
            
            #reshaping
            imgs_yellow_fl = imgs_yellow_fl.reshape(int(batch_size/4),28*28*3)
            Y_repeated = Y_repeated.reshape(int(batch_size/4),4096)
            
            #appending with embedding yellow fruit
            imgs_yellow_fl_with_emb = np.concatenate((imgs_yellow_fl, Y_repeated),axis=1)
            
            
            
            imgs = np.concatenate((imgs_green_fr_with_emb, imgs_purple_fr_with_emb),axis=0)
            imgs = np.concatenate((imgs, imgs_red_fl_with_emb),axis=0)
            imgs = np.concatenate((imgs, imgs_yellow_fl_with_emb),axis=0)
            
            
            #Generating noise
            noise = np.random.normal(0, 1, (batch_size, 500))
            noise = noise.reshape(batch_size,500)
            
            
            imgs = np.concatenate((imgs, noise),axis=1)
            
            
            # Sample generator input
            #noise = np.random.normal(0, 1, (batch_size, 100))
            
            
            #Generating noise
            noise = np.random.normal(0, 1, (batch_size, 500))
            noise = noise.reshape(batch_size,500)

            text_embed = np.concatenate((G_repeated,P_repeated),axis=0)
            text_embed = np.concatenate((text_embed,R_repeated),axis=0)
            text_embed = np.concatenate((text_embed,Y_repeated),axis=0)  
            
            
            text_embed = np.concatenate((text_embed, noise),axis=1)
            
            
            # Generate a batch of new images
            gen_imgs = self.generator.predict(text_embed)
            
            
            print (gen_imgs.shape)
            print (text_embed.shape)
            
            gen_imgs = gen_imgs.reshape(batch_size, 28*28*3)
            print (text_embed.shape)
            
            #concatenate embeddings wit the generated images
            gen_imgs = np.concatenate((gen_imgs, text_embed),axis=1)
            

            # Train the discriminator
            d_loss_real = self.discriminator.train_on_batch(imgs, valid)
            d_loss_fake = self.discriminator.train_on_batch(gen_imgs, fake)
            d_loss = 0.5 * np.add(d_loss_real, d_loss_fake)

            # ---------------------
            #  Train Generator
            # ---------------------

            # Sample generator input
            #noise = np.random.normal(0, 1, (batch_size, 100))
            # Train the generator
            g_loss = self.combined.train_on_batch(text_embed, valid)

            # Plot the progress
            print ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))
            file = open ("128_batch","w+")
            file.write ("%d [D loss: %f, acc.: %.2f%%] [G loss: %f]" % (epoch, d_loss[0], 100*d_loss[1], g_loss))
            

            # If at save interval => save generated image samples
            if epoch % save_interval == 0:
                self.save_imgs(epoch, text_embed)
                
            

    def save_imgs(self, epoch, text_embed):
        r, c = 4, 8
        #noise = np.random.normal(0, 1, (r * c, 100))
        gen_imgs = self.generator.predict(text_embed)
        
        #dimensions
        print(gen_imgs.shape)
        gen_imgs = gen_imgs.reshape(32,28,28,3) #hardcoded batch-size 32

        # Rescale images 0 - 1
        gen_imgs = (1/2.5) * gen_imgs + 0.5

        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt, :,:,:])
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("output_banana_pear/%d.png" % epoch)
        plt.close()

In [51]:
if __name__ == '__main__':
    gan = GAN()
    gan.train(epochs=40000, batch_size=32, save_interval=50)

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
dense_85 (Dense)             (None, 512)               3557888   
_________________________________________________________________
leaky_re_lu_61 (LeakyReLU)   (None, 512)               0         
_________________________________________________________________
dense_86 (Dense)             (None, 256)               131328    
_________________________________________________________________
leaky_re_lu_62 (LeakyReLU)   (None, 256)               0         
_________________________________________________________________
dense_87 (Dense)             (None, 1)                 257       
Total params: 3,689,473
Trainable params: 3,689,473
Non-trainable params: 0
_________________________________________________________________
_________________________________________________________________
Layer (type)                 Output Shape              Param #   


/usr/local/lib/python3.4/dist-packages/keras/engine/training.py:975: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


0 [D loss: 0.727851, acc.: 42.19%] [G loss: 0.822852]
(32, 2352)
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
1 [D loss: 0.306683, acc.: 84.38%] [G loss: 1.266629]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
2 [D loss: 0.192715, acc.: 100.00%] [G loss: 1.750886]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
3 [D loss: 0.106189, acc.: 100.00%] [G loss: 2.187231]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
4 [D loss: 0.078406, acc.: 100.00%] [G loss: 2.566250]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
5 [D loss: 0.055106, acc.: 100.00%] [G loss: 2.834617]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
6 [D loss: 0.039389, acc.: 100.00%] [G loss: 3.114841]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
7 [D loss: 0.032840, acc.: 100.00%] [G loss: 3.364912]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
8 [D loss: 0.020440, acc.: 100.00%] [G loss: 3.645476]
(8, 28, 

70 [D loss: 0.072598, acc.: 98.44%] [G loss: 12.957843]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
71 [D loss: 0.067539, acc.: 96.88%] [G loss: 13.094425]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
72 [D loss: 2.294725, acc.: 56.25%] [G loss: 9.991640]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
73 [D loss: 0.050812, acc.: 100.00%] [G loss: 11.559126]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
74 [D loss: 0.716359, acc.: 57.81%] [G loss: 12.030023]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
75 [D loss: 0.043185, acc.: 100.00%] [G loss: 12.376772]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
76 [D loss: 0.276157, acc.: 85.94%] [G loss: 13.083971]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
77 [D loss: 0.085162, acc.: 100.00%] [G loss: 11.229115]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
78 [D loss: 0.353457, acc.: 78.12%] [G loss: 14.114928]
(8, 28

140 [D loss: 0.428187, acc.: 78.12%] [G loss: 7.123471]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
141 [D loss: 0.378121, acc.: 79.69%] [G loss: 7.523140]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
142 [D loss: 0.684268, acc.: 45.31%] [G loss: 7.564963]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
143 [D loss: 0.432601, acc.: 81.25%] [G loss: 7.112006]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
144 [D loss: 0.350143, acc.: 84.38%] [G loss: 7.117607]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
145 [D loss: 0.494923, acc.: 81.25%] [G loss: 8.026272]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
146 [D loss: 0.711744, acc.: 54.69%] [G loss: 7.206717]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
147 [D loss: 0.291197, acc.: 93.75%] [G loss: 7.126602]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
148 [D loss: 0.396813, acc.: 85.94%] [G loss: 7.879790]
(8, 28, 

...

39680 [D loss: 0.129847, acc.: 95.31%] [G loss: 3.263743]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39681 [D loss: 0.484171, acc.: 82.81%] [G loss: 2.931441]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39682 [D loss: 0.226097, acc.: 89.06%] [G loss: 3.439806]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39683 [D loss: 0.162965, acc.: 93.75%] [G loss: 3.455780]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39684 [D loss: 0.039075, acc.: 100.00%] [G loss: 4.051189]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39685 [D loss: 0.286028, acc.: 92.19%] [G loss: 3.709935]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39686 [D loss: 0.079463, acc.: 96.88%] [G loss: 3.827313]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39687 [D loss: 0.240574, acc.: 90.62%] [G loss: 3.424970]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39688 [D loss: 0.189733, acc.: 93.75%] [G loss:

39749 [D loss: 0.085683, acc.: 96.88%] [G loss: 3.242571]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39750 [D loss: 0.135591, acc.: 93.75%] [G loss: 4.278356]
(32, 2352)
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39751 [D loss: 0.167419, acc.: 93.75%] [G loss: 4.001832]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39752 [D loss: 0.191976, acc.: 93.75%] [G loss: 3.625127]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39753 [D loss: 0.151408, acc.: 96.88%] [G loss: 3.517132]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39754 [D loss: 0.119529, acc.: 96.88%] [G loss: 3.882420]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39755 [D loss: 0.083830, acc.: 98.44%] [G loss: 3.857641]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39756 [D loss: 0.094621, acc.: 98.44%] [G loss: 3.707007]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39757 [D loss: 0.244380, acc.: 89.06%

39818 [D loss: 0.086290, acc.: 98.44%] [G loss: 3.877932]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39819 [D loss: 0.259290, acc.: 90.62%] [G loss: 4.170167]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39820 [D loss: 0.215801, acc.: 95.31%] [G loss: 3.023225]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39821 [D loss: 0.300563, acc.: 89.06%] [G loss: 2.653522]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39822 [D loss: 0.210013, acc.: 92.19%] [G loss: 3.603188]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39823 [D loss: 0.103091, acc.: 96.88%] [G loss: 3.625550]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39824 [D loss: 0.383538, acc.: 90.62%] [G loss: 3.678758]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39825 [D loss: 0.256960, acc.: 90.62%] [G loss: 3.390924]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39826 [D loss: 0.282429, acc.: 90.62%] [G loss: 

39887 [D loss: 0.332140, acc.: 89.06%] [G loss: 3.175595]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39888 [D loss: 0.120761, acc.: 95.31%] [G loss: 3.669980]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39889 [D loss: 0.062682, acc.: 98.44%] [G loss: 3.853482]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39890 [D loss: 0.250595, acc.: 92.19%] [G loss: 3.644162]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39891 [D loss: 0.303552, acc.: 90.62%] [G loss: 3.075242]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39892 [D loss: 0.125929, acc.: 93.75%] [G loss: 4.637901]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39893 [D loss: 0.338113, acc.: 92.19%] [G loss: 3.822528]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39894 [D loss: 0.133469, acc.: 93.75%] [G loss: 3.070793]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39895 [D loss: 0.174567, acc.: 95.31%] [G loss: 

39956 [D loss: 0.195863, acc.: 93.75%] [G loss: 3.266704]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39957 [D loss: 0.250954, acc.: 90.62%] [G loss: 3.314908]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39958 [D loss: 0.141492, acc.: 95.31%] [G loss: 3.526728]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39959 [D loss: 0.120285, acc.: 96.88%] [G loss: 4.087904]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39960 [D loss: 0.328555, acc.: 90.62%] [G loss: 3.064862]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39961 [D loss: 0.219608, acc.: 93.75%] [G loss: 2.677148]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39962 [D loss: 0.139585, acc.: 96.88%] [G loss: 2.867717]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39963 [D loss: 0.126017, acc.: 96.88%] [G loss: 3.051230]
(8, 28, 28, 3)
(8, 1, 4096)
(32, 2352)
(32, 4596)
(32, 4596)
39964 [D loss: 0.160683, acc.: 93.75%] [G loss: 

In [52]:
    with open('generator.json', 'w') as f:
        f.write(gan.generator.to_json())
    gan.generator.save('generator.h5')


In [54]:
    
    
    # Returns a compiled model identical to the previous one
    model = load_model('generator.h5')
    
    # Plot the image 
    r, c = 1, 1
    #noise = np.random.normal(0, 1, (r * c, 100))
    
    
    #extract the text_embedding
    purple_banana = np.genfromtxt('purplebanana.csv',delimiter=",").reshape(1,4096);
    
    #Generating noise
    noise = np.random.normal(0, 1, (1, 500))
    noise = noise.reshape(1,500)
    
    #combine noise
    text_embed = np.concatenate((purple_banana, noise),axis=1)    
    
    gen_imgs = model.predict(text_embed)
        
    #dimensions
    print(gen_imgs.shape)
    gen_imgs = gen_imgs.reshape(1,28,28,3) #hardcoded batch-size 32

    # Rescale images 0 - 1
    gen_imgs = (1/2.5) * gen_imgs + 0.5

    fig, axs = plt.subplots(r, c)
    cnt = 0

    axs.imshow(gen_imgs[cnt, :,:,:])
    axs.axis('off')
    
    fig.savefig("generated_image_after_training/purple_banana.png")
    plt.close()
    

/usr/local/lib/python3.4/dist-packages/keras/models.py:282: UserWarning: No training configuration found in save file: the model was *not* compiled. Compile it manually.
  warnings.warn('No training configuration found in save file: '


(1, 2352)


In [56]:
    #extract the text_embedding
    red_pear = np.genfromtxt('redpear.csv',delimiter=",").reshape(1,4096);
    
    #Generating noise
    noise = np.random.normal(0, 1, (1, 500))
    noise = noise.reshape(1,500)
    
    #combine noise
    text_embed = np.concatenate((red_pear, noise),axis=1)    
    
    gen_imgs = model.predict(text_embed)
        
    #dimensions
    print(gen_imgs.shape)
    gen_imgs = gen_imgs.reshape(1,28,28,3) #hardcoded batch-size 32

    # Rescale images 0 - 1
    gen_imgs = (1/2.5) * gen_imgs + 0.5

    fig, axs = plt.subplots(r, c)
    cnt = 0

    axs.imshow(gen_imgs[cnt, :,:,:])
    axs.axis('off')
    
    fig.savefig("generated_image_after_training/red_pear.png")
    plt.close()

(1, 2352)


In [57]:
    #extract the text_embedding
    yellow_pear = np.genfromtxt('yellowpear.csv',delimiter=",").reshape(1,4096);
    
    #Generating noise
    noise = np.random.normal(0, 1, (1, 500))
    noise = noise.reshape(1,500)
    
    #combine noise
    text_embed = np.concatenate((yellow_pear, noise),axis=1)    
    
    gen_imgs = model.predict(text_embed)
        
    #dimensions
    print(gen_imgs.shape)
    gen_imgs = gen_imgs.reshape(1,28,28,3) #hardcoded batch-size 32

    # Rescale images 0 - 1
    gen_imgs = (1/2.5) * gen_imgs + 0.5

    fig, axs = plt.subplots(r, c)
    cnt = 0

    axs.imshow(gen_imgs[cnt, :,:,:])
    axs.axis('off')
    
    fig.savefig("generated_image_after_training/yellow_pear.png")
    plt.close()

(1, 2352)


In [58]:
    #extract the text_embedding
    green_banana = np.genfromtxt('greenbanana.csv',delimiter=",").reshape(1,4096);
    
    #Generating noise
    noise = np.random.normal(0, 1, (1, 500))
    noise = noise.reshape(1,500)
    
    #combine noise
    text_embed = np.concatenate((green_banana, noise),axis=1)    
    
    gen_imgs = model.predict(text_embed)
        
    #dimensions
    print(gen_imgs.shape)
    gen_imgs = gen_imgs.reshape(1,28,28,3) #hardcoded batch-size 32

    # Rescale images 0 - 1
    gen_imgs = (1/2.5) * gen_imgs + 0.5

    fig, axs = plt.subplots(r, c)
    cnt = 0

    axs.imshow(gen_imgs[cnt, :,:,:])
    axs.axis('off')
    
    fig.savefig("generated_image_after_training/green_banana.png")
    plt.close()

(1, 2352)
